In [1]:
import numpy as np
import pandas as pd 
from sklearn.metrics.pairwise import sigmoid_kernel
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity
from gensim.models import Word2Vec
from gensim.models import KeyedVectors
import gensim
import numpy as np
import pandas as pd
from tqdm import tqdm
from collections import defaultdict


In [2]:
products = pd.read_csv(r'.\Recommeder\Data\flipkart_com-ecommerce_sample.csv')
print(products.shape ,len(products['product_name'].unique()),len(products['uniq_id'].unique()))

(20000, 15) 12676 20000


In [3]:

tfv = TfidfVectorizer(max_features=None,
                     strip_accents='unicode',
                     analyzer='word',
                     min_df=10,
                     token_pattern=r'\w{1,}',
                     ngram_range=(1,3),#take the combination of 1-3 different kind of words
                     stop_words='english')#removes all the unnecessary characters like the,in etc.
products['description'] = products['description'].fillna('')
tfv_matrix = tfv.fit_transform(products['description'])

indices = pd.Series(products.index,index=products['product_name']).drop_duplicates()
pidToidx = pd.Series(products.index,index=products['uniq_id']).drop_duplicates()






In [6]:
#save the tfv_matrix in a file
import pickle
pickle.dump(tfv_matrix, open("tfv_matrix.pkl", "wb"))


In [4]:
sig = sigmoid_kernel(tfv_matrix,tfv_matrix)


In [5]:
# save sig in a file
np.save('sig.npy', sig)



In [8]:
def getNearestProduct(unknownWord , topk=10 ):
    newSig = sigmoid_kernel(tfv_matrix , tfv.transform([unknownWord]))
    # idx = np.argsort(
    sigScore = list(enumerate(newSig))
    sigScore = sorted(sigScore , key=lambda x:x[1] , reverse=True)
    sigScore = sigScore[0:topk]
    idx = [i[0] for i in sigScore]

    # print(newSig.shape ,newSig)

    productNames = []
    for i in idx:
        productNames.append(products['product_name'].iloc[i])
    return productNames

    


In [9]:
def product_recommendation(title,sig=sig , topk=10):
    if title not in products['product_name'].unique():
        return getNearestProduct(title , topk)
    
    indx = indices[title][0]
    # print(indx[]
    # print(indx)
    # getting pairwise similarity scores 
    sig_scores = []
    for i in range(len(sig[indx])):
        sig_scores.append((i,sig[indx][i]))
    # print(len(sig_scores) , len(sig[0]))
    # for i in range(len(sig[indx])):
    #     sig_score[i] = sorted(sig_scores , key=lambda x:x[1] , reverse=True)
    sig_scores = sorted(sig_scores , key=lambda x:x[1] , reverse=True)

    
    sig_scores = sig_scores[1:topk+1]
    
    # #product indexes
    product_indices = [i[0] for i in sig_scores]
    
    # #Top 10 most similar products
    return products['product_name'].iloc[product_indices].unique()


print(product_recommendation("jeans"))


["Ben Carter Slim Fit Men's Jeans", "Provogue Slim Fit Men's Jeans", "Provogue Slim Fit Men's Jeans", "I cube Slim Fit Boy's Jeans", "StyloFashionGarments slim Fit Women's Jeans", "Dassler Slim Fit Women's Multicolor Jeans", "Dassler Slim Fit Women's Multicolor Jeans", "Flying Port Slim Fit Men's Blue Jeans", "Flying Port Slim Fit Men's Blue Jeans", "Mankoose Regular fit Fit Boy's Jeans"]


In [51]:
product_name = "Rialto Boots"
product_recommendation(product_name , sig=sig , topk=10)

["Alisha Solid Women's Cycling Shorts",
 'FabHomeDecor Fabric Double Sofa Bed',
 'AW Bellies',
 "Alisha Solid Women's Cycling Shorts",
 'Sicons All Purpose Arnica Dog Shampoo',
 'Eternal Gandhi Super Series Crystal Paper Weights  with Silver Finish',
 "Alisha Solid Women's Cycling Shorts",
 'FabHomeDecor Fabric Double Sofa Bed',
 'dilli bazaaar Bellies, Corporate Casuals, Casuals',
 "Alisha Solid Women's Cycling Shorts"]

In [5]:
transactions_path = r".\Recommeder\Data\transaction.csv"

transaction_table = pd.read_csv(transactions_path)

In [53]:
def product_recommendation_UserPurchases(products_bought , sig  , topK):
    # idx = pidToidx[products_bought]
    idx = []
    for i in range(len(products_bought)):
        idx.append(pidToidx[products_bought[i]])
    

    # conver idx to df
    # idx = pd.DataFrame(idx)
    # print(idx.shape)
    # get pairwise similarity scores
    sig_scores = []
    for i in idx:
        for j in range(len(sig[i])):
            # do not include the product itself and the products already bought by the user
            if j != i and j not in products_bought:
                # if len(sig_scores)==0 or abs(sig_scores[-1][1] - sig[i][j]) >= 0.000023*sig_scores[-1][1]:
                    sig_scores.append((j, sig[i][j]))

    
    # sort the products based on similarity scores
    sig_scores = sorted(sig_scores, key=lambda x: x[1], reverse=True)
    print(sig_scores)

    sig_scores = sig_scores[:50]
    product_indices = []
    for i in sig_scores:
        product_indices.append(i[0])
    product_name = products['product_name'].iloc[product_indices]
    return product_name.unique()

uid = "360a74c1-1039-4592-bf88-848e7e2e1eb7"
reccomdations = []
products_bought = transaction_table[transaction_table['UID'] == uid]['PID'].tolist()
reccomdations = product_recommendation_UserPurchases(products_bought , sig , 10)

print("\nTop Recommended products are: \n")
print("Product bought by user: ", len(products_bought))
# print(products_bought)
# print("------------------------------------")
print("Recommended products: ", len(reccomdations))
print(reccomdations)


[(6056, 0.7616121684208375), (7080, 0.7616121684208375), (2788, 0.7616121684208375), (3766, 0.7616121684208375), (4226, 0.7616121684208375), (1648, 0.7616121684208375), (1650, 0.7616121684208375), (1653, 0.7616121684208375), (1656, 0.7616121684208375), (1671, 0.7616121684208375), (1673, 0.7616121684208375), (1697, 0.7616121684208375), (1701, 0.7616121684208375), (1706, 0.7616121684208375), (1713, 0.7616121684208375), (1716, 0.7616121684208375), (1724, 0.7616121684208375), (1732, 0.7616121684208375), (1743, 0.7616121684208375), (1757, 0.7616121684208375), (1764, 0.7616121684208375), (1770, 0.7616121684208375), (1786, 0.7616121684208375), (1789, 0.7616121684208375), (1793, 0.7616121684208375), (1809, 0.7616121684208375), (1812, 0.7616121684208375), (1823, 0.7616121684208375), (1840, 0.7616121684208375), (1873, 0.7616121684208375), (1875, 0.7616121684208375), (1877, 0.7616121684208375), (1881, 0.7616121684208375), (1897, 0.7616121684208375), (1901, 0.7616121684208375), (1904, 0.7616121684